In [ ]:
###############################################

In [ ]:
!pip install transformers
!pip install datasets
!pip install tiktoken
!pip install wandb
!pip install tqdm

In [87]:
import pandas as pd
data = pd.read_json('data/mtg_char/default-cards-20230313210730.json')

In [88]:
# peek at the data
print(data.shape)
data.head()

(80731, 84)


object                                    id  \
0   card  0000579f-7b35-4ed3-b44c-db2a538066fe   
1   card  00006596-1166-4a79-8443-ca9f82e6db4e   
2   card  0000a54c-a511-4925-92dc-01b937f9afad   
3   card  0000cd57-91fe-411f-b798-646e965eec37   
4   card  00012bd8-ed68-4978-a22d-f450c8a6e048   

                              oracle_id multiverse_ids  mtgo_id  mtgo_foil_id  \
0  44623693-51d6-49ad-8cd7-140505caf02f       [109722]  25527.0       25528.0   
1  8ae3562f-28b7-4462-96ed-be0cf7052ccc       [189637]  34586.0       34587.0   
2  dc4e2134-f0c2-49aa-9ea3-ebf83af1445c             []      NaN           NaN   
3  9f0d82ae-38bf-45d8-8cda-982b6ead1d72       [435231]  65170.0       65171.0   
4  5aa12aff-db3c-4be5-822b-3afdf536b33e         [1278]      NaN           NaN   

   tcgplayer_id  cardmarket_id           name lang  ... tcgplayer_etched_id  \
0       14240.0        13850.0    Fury Sliver   en  ...                 NaN   
1       33347.0        21851.0  Kor Outfitter   en  ...                 NaN   
2       98659.0            NaN         Spirit   en  ...                 NaN   
3      145764.0       301766.0  Siren Lookout   en  ...                 NaN   
4        1623.0         5664.0            Web   en  ...                 NaN   

  attraction_lights color_indicator variation_of  life_modifier hand_modifier  \
0               NaN             NaN          NaN            NaN           NaN   
1               NaN             NaN          NaN            NaN           NaN   
2               NaN             NaN          NaN            NaN           NaN   
3               NaN             NaN          NaN            NaN           NaN   
4               NaN             NaN          NaN            NaN           NaN   

  printed_type_line printed_text  content_warning flavor_name  
0               NaN          NaN              NaN         NaN  
1               NaN          NaN              NaN         NaN  
2               NaN          NaN              NaN         NaN  
3               NaN          NaN              NaN         NaN  
4               NaN          NaN              NaN         NaN  

[5 rows x 84 columns]

In [89]:
# filter out cards that are not in english
data = data[data['lang'] == 'en']
print(data.shape)
data.head()

(78312, 84)


object                                    id  \
0   card  0000579f-7b35-4ed3-b44c-db2a538066fe   
1   card  00006596-1166-4a79-8443-ca9f82e6db4e   
2   card  0000a54c-a511-4925-92dc-01b937f9afad   
3   card  0000cd57-91fe-411f-b798-646e965eec37   
4   card  00012bd8-ed68-4978-a22d-f450c8a6e048   

                              oracle_id multiverse_ids  mtgo_id  mtgo_foil_id  \
0  44623693-51d6-49ad-8cd7-140505caf02f       [109722]  25527.0       25528.0   
1  8ae3562f-28b7-4462-96ed-be0cf7052ccc       [189637]  34586.0       34587.0   
2  dc4e2134-f0c2-49aa-9ea3-ebf83af1445c             []      NaN           NaN   
3  9f0d82ae-38bf-45d8-8cda-982b6ead1d72       [435231]  65170.0       65171.0   
4  5aa12aff-db3c-4be5-822b-3afdf536b33e         [1278]      NaN           NaN   

   tcgplayer_id  cardmarket_id           name lang  ... tcgplayer_etched_id  \
0       14240.0        13850.0    Fury Sliver   en  ...                 NaN   
1       33347.0        21851.0  Kor Outfitter   en  ...                 NaN   
2       98659.0            NaN         Spirit   en  ...                 NaN   
3      145764.0       301766.0  Siren Lookout   en  ...                 NaN   
4        1623.0         5664.0            Web   en  ...                 NaN   

  attraction_lights color_indicator variation_of  life_modifier hand_modifier  \
0               NaN             NaN          NaN            NaN           NaN   
1               NaN             NaN          NaN            NaN           NaN   
2               NaN             NaN          NaN            NaN           NaN   
3               NaN             NaN          NaN            NaN           NaN   
4               NaN             NaN          NaN            NaN           NaN   

  printed_type_line printed_text  content_warning flavor_name  
0               NaN          NaN              NaN         NaN  
1               NaN          NaN              NaN         NaN  
2               NaN          NaN              NaN         NaN  
3               NaN          NaN              NaN         NaN  
4               NaN          NaN              NaN         NaN  

[5 rows x 84 columns]

In [90]:
# Keep only normal cards
data = data[data['layout'] == 'normal']

In [91]:
data.head()

object                                    id  \
0   card  0000579f-7b35-4ed3-b44c-db2a538066fe   
1   card  00006596-1166-4a79-8443-ca9f82e6db4e   
3   card  0000cd57-91fe-411f-b798-646e965eec37   
4   card  00012bd8-ed68-4978-a22d-f450c8a6e048   
5   card  0001f1ef-b957-4a55-b47f-14839cdbab6f   

                              oracle_id multiverse_ids  mtgo_id  mtgo_foil_id  \
0  44623693-51d6-49ad-8cd7-140505caf02f       [109722]  25527.0       25528.0   
1  8ae3562f-28b7-4462-96ed-be0cf7052ccc       [189637]  34586.0       34587.0   
3  9f0d82ae-38bf-45d8-8cda-982b6ead1d72       [435231]  65170.0       65171.0   
4  5aa12aff-db3c-4be5-822b-3afdf536b33e         [1278]      NaN           NaN   
5  ef027846-be81-4959-a6b5-56bd01b1e68a       [472997]  78170.0           NaN   

   tcgplayer_id  cardmarket_id              name lang  ...  \
0       14240.0        13850.0       Fury Sliver   en  ...   
1       33347.0        21851.0     Kor Outfitter   en  ...   
3      145764.0       301766.0     Siren Lookout   en  ...   
4        1623.0         5664.0               Web   en  ...   
5      198861.0       400134.0  Venerable Knight   en  ...   

  tcgplayer_etched_id attraction_lights color_indicator variation_of  \
0                 NaN               NaN             NaN          NaN   
1                 NaN               NaN             NaN          NaN   
3                 NaN               NaN             NaN          NaN   
4                 NaN               NaN             NaN          NaN   
5                 NaN               NaN             NaN          NaN   

   life_modifier hand_modifier printed_type_line printed_text  \
0            NaN           NaN               NaN          NaN   
1            NaN           NaN               NaN          NaN   
3            NaN           NaN               NaN          NaN   
4            NaN           NaN               NaN          NaN   
5            NaN           NaN               NaN          NaN   

   content_warning flavor_name  
0              NaN         NaN  
1              NaN         NaN  
3              NaN         NaN  
4              NaN         NaN  
5              NaN         NaN  

[5 rows x 84 columns]

In [92]:
# remove cards with duplicate names
data = data.drop_duplicates(subset=['name'])
print(data.shape)
data.head()

(25438, 84)


object                                    id  \
0   card  0000579f-7b35-4ed3-b44c-db2a538066fe   
1   card  00006596-1166-4a79-8443-ca9f82e6db4e   
3   card  0000cd57-91fe-411f-b798-646e965eec37   
4   card  00012bd8-ed68-4978-a22d-f450c8a6e048   
5   card  0001f1ef-b957-4a55-b47f-14839cdbab6f   

                              oracle_id multiverse_ids  mtgo_id  mtgo_foil_id  \
0  44623693-51d6-49ad-8cd7-140505caf02f       [109722]  25527.0       25528.0   
1  8ae3562f-28b7-4462-96ed-be0cf7052ccc       [189637]  34586.0       34587.0   
3  9f0d82ae-38bf-45d8-8cda-982b6ead1d72       [435231]  65170.0       65171.0   
4  5aa12aff-db3c-4be5-822b-3afdf536b33e         [1278]      NaN           NaN   
5  ef027846-be81-4959-a6b5-56bd01b1e68a       [472997]  78170.0           NaN   

   tcgplayer_id  cardmarket_id              name lang  ...  \
0       14240.0        13850.0       Fury Sliver   en  ...   
1       33347.0        21851.0     Kor Outfitter   en  ...   
3      145764.0       301766.0     Siren Lookout   en  ...   
4        1623.0         5664.0               Web   en  ...   
5      198861.0       400134.0  Venerable Knight   en  ...   

  tcgplayer_etched_id attraction_lights color_indicator variation_of  \
0                 NaN               NaN             NaN          NaN   
1                 NaN               NaN             NaN          NaN   
3                 NaN               NaN             NaN          NaN   
4                 NaN               NaN             NaN          NaN   
5                 NaN               NaN             NaN          NaN   

   life_modifier hand_modifier printed_type_line printed_text  \
0            NaN           NaN               NaN          NaN   
1            NaN           NaN               NaN          NaN   
3            NaN           NaN               NaN          NaN   
4            NaN           NaN               NaN          NaN   
5            NaN           NaN               NaN          NaN   

   content_warning flavor_name  
0              NaN         NaN  
1              NaN         NaN  
3              NaN         NaN  
4              NaN         NaN  
5              NaN         NaN  

[5 rows x 84 columns]

In [93]:
# now that we dont have any other languages, we can drop the lang column
data = data.drop(columns=['lang'])
print(data.shape)
data.head()

(25438, 83)


object                                    id  \
0   card  0000579f-7b35-4ed3-b44c-db2a538066fe   
1   card  00006596-1166-4a79-8443-ca9f82e6db4e   
3   card  0000cd57-91fe-411f-b798-646e965eec37   
4   card  00012bd8-ed68-4978-a22d-f450c8a6e048   
5   card  0001f1ef-b957-4a55-b47f-14839cdbab6f   

                              oracle_id multiverse_ids  mtgo_id  mtgo_foil_id  \
0  44623693-51d6-49ad-8cd7-140505caf02f       [109722]  25527.0       25528.0   
1  8ae3562f-28b7-4462-96ed-be0cf7052ccc       [189637]  34586.0       34587.0   
3  9f0d82ae-38bf-45d8-8cda-982b6ead1d72       [435231]  65170.0       65171.0   
4  5aa12aff-db3c-4be5-822b-3afdf536b33e         [1278]      NaN           NaN   
5  ef027846-be81-4959-a6b5-56bd01b1e68a       [472997]  78170.0           NaN   

   tcgplayer_id  cardmarket_id              name released_at  ...  \
0       14240.0        13850.0       Fury Sliver  2006-10-06  ...   
1       33347.0        21851.0     Kor Outfitter  2009-10-02  ...   
3      145764.0       301766.0     Siren Lookout  2017-09-29  ...   
4        1623.0         5664.0               Web  1994-04-01  ...   
5      198861.0       400134.0  Venerable Knight  2019-10-04  ...   

  tcgplayer_etched_id attraction_lights color_indicator  variation_of  \
0                 NaN               NaN             NaN           NaN   
1                 NaN               NaN             NaN           NaN   
3                 NaN               NaN             NaN           NaN   
4                 NaN               NaN             NaN           NaN   
5                 NaN               NaN             NaN           NaN   

  life_modifier hand_modifier printed_type_line  printed_text content_warning  \
0           NaN           NaN               NaN           NaN             NaN   
1           NaN           NaN               NaN           NaN             NaN   
3           NaN           NaN               NaN           NaN             NaN   
4           NaN           NaN               NaN           NaN             NaN   
5           NaN           NaN               NaN           NaN             NaN   

  flavor_name  
0         NaN  
1         NaN  
3         NaN  
4         NaN  
5         NaN  

[5 rows x 83 columns]

In [94]:
data = data.drop(columns=['mtgo_id', 'mtgo_foil_id', 'arena_id', 'tcgplayer_id', 'cardmarket_id', 'legalities', 'games', 'reserved', 'foil', 'nonfoil', 'finishes', 'oversized', 'promo', 'reprint', 'variation', 'artist', 'artist_ids', 'illustration_id', 'border_color', 'booster', 'story_spotlight', 'edhrec_rank', 'penny_rank','prices', 'promo_types', 'arena_id', 'preview', 'security_stamp', 'tcgplayer_etched_id', 'variation_of','released_at', 'set_id','set', 'set_uri', 'set_search_uri', 'scryfall_set_uri', 'rulings_uri', 'prints_search_uri', 'card_back_id', 'frame', 'related_uris'])

In [95]:
data = data.drop(columns=['object', 'id', 'oracle_id', 'uri', 'scryfall_uri', 'layout', 'highres_image', 'image_status', 'printed_name', 'card_faces', 'attraction_lights', 'color_indicator', 'color_indicator', 'life_modifier', 'hand_modifier', 'printed_type_line', 'printed_text', 'content_warning', 'flavor_name'])

In [96]:
data = data.drop(columns=['full_art', 'textless', 'all_parts', 'produced_mana', 'watermark', 'loyalty', 'frame_effects', 'digital', 'cmc' ])

In [97]:
data = data.drop(columns=['keywords', 'collector_number', 'colors', 'color_identity'])

In [98]:
print(data.shape)
data.head()

(25438, 12)


multiverse_ids              name  \
0       [109722]       Fury Sliver   
1       [189637]     Kor Outfitter   
3       [435231]     Siren Lookout   
4         [1278]               Web   
5       [472997]  Venerable Knight   

                                          image_uris mana_cost  \
0  {'small': 'https://cards.scryfall.io/small/fro...    {5}{R}   
1  {'small': 'https://cards.scryfall.io/small/fro...    {W}{W}   
3  {'small': 'https://cards.scryfall.io/small/fro...    {2}{U}   
4  {'small': 'https://cards.scryfall.io/small/fro...       {G}   
5  {'small': 'https://cards.scryfall.io/small/fro...       {W}   

                 type_line                                        oracle_text  \
0        Creature — Sliver           All Sliver creatures have double strike.   
1   Creature — Kor Soldier  When Kor Outfitter enters the battlefield, you...   
3  Creature — Siren Pirate  Flying\nWhen Siren Lookout enters the battlefi...   
4       Enchantment — Aura  Enchant creature (Target a creature as you cas...   
5  Creature — Human Knight  When Venerable Knight dies, put a +1/+1 counte...   

  power toughness            set_name   set_type    rarity  \
0     3         3         Time Spiral  expansion  uncommon   
1     2         2            Zendikar  expansion    common   
3     1         2              Ixalan  expansion    common   
4   NaN       NaN     Revised Edition       core      rare   
5     2         1  Throne of Eldraine  expansion  uncommon   

                                         flavor_text  
0  "A rift opened, and our arrows were abruptly s...  
1  "We take only what we need to survive. Believe...  
3                                                NaN  
4                                                NaN  
5  "May this blade guide you on your great journe...

In [99]:
data['oracle_text'] = data.apply(lambda x: x['oracle_text'].replace(x['name'], '<card_name>'), axis=1)


In [100]:
print(data.shape)
data.head()

(25438, 12)


multiverse_ids              name  \
0       [109722]       Fury Sliver   
1       [189637]     Kor Outfitter   
3       [435231]     Siren Lookout   
4         [1278]               Web   
5       [472997]  Venerable Knight   

                                          image_uris mana_cost  \
0  {'small': 'https://cards.scryfall.io/small/fro...    {5}{R}   
1  {'small': 'https://cards.scryfall.io/small/fro...    {W}{W}   
3  {'small': 'https://cards.scryfall.io/small/fro...    {2}{U}   
4  {'small': 'https://cards.scryfall.io/small/fro...       {G}   
5  {'small': 'https://cards.scryfall.io/small/fro...       {W}   

                 type_line                                        oracle_text  \
0        Creature — Sliver           All Sliver creatures have double strike.   
1   Creature — Kor Soldier  When <card_name> enters the battlefield, you m...   
3  Creature — Siren Pirate  Flying\nWhen <card_name> enters the battlefiel...   
4       Enchantment — Aura  Enchant creature (Target a creature as you cas...   
5  Creature — Human Knight  When <card_name> dies, put a +1/+1 counter on ...   

  power toughness            set_name   set_type    rarity  \
0     3         3         Time Spiral  expansion  uncommon   
1     2         2            Zendikar  expansion    common   
3     1         2              Ixalan  expansion    common   
4   NaN       NaN     Revised Edition       core      rare   
5     2         1  Throne of Eldraine  expansion  uncommon   

                                         flavor_text  
0  "A rift opened, and our arrows were abruptly s...  
1  "We take only what we need to survive. Believe...  
3                                                NaN  
4                                                NaN  
5  "May this blade guide you on your great journe...

In [101]:
# Build a string representation of each card to be saved out as a text file.
# Card data will be represented as a string with the following format:
# "<|endoftext|>{card_name} | ?{mana_cost} | {type_line} | {rarity} | ?{oracle_text} | ?{flavor_text} | ?{power} | ?{toughness}<|endoftext|>"
# The ? indicates that the field may be empty.

# start of text token
sot = "<|startoftext|>"
# end of text token
eot = "<|endoftext|>"
# pad token
pad = "<|pad|>"

card_data = []

for index, row in data.iterrows():
    card_data.append(f" {eot} {row['name']} | {row['mana_cost']} | {row['type_line']} | {row['rarity']} | {row['oracle_text']} | {row['flavor_text']} | {row['power']} | {row['toughness']} {eot} \n")

# sample the first 10 cards
card_data[:10]


[' <|endoftext|> Fury Sliver | {5}{R} | Creature — Sliver | uncommon | All Sliver creatures have double strike. | "A rift opened, and our arrows were abruptly stilled. To move was to push the world. But the sliver\'s claw still twitched, red wounds appeared in Thed\'s chest, and ribbons of blood hung in the air."\n—Adom Capashen, Benalish hero | 3 | 3 <|endoftext|> \n',
 ' <|endoftext|> Kor Outfitter | {W}{W} | Creature — Kor Soldier | common | When <card_name> enters the battlefield, you may attach target Equipment you control to target creature you control. | "We take only what we need to survive. Believe me, you will need this." | 2 | 2 <|endoftext|> \n',
 " <|endoftext|> Siren Lookout | {2}{U} | Creature — Siren Pirate | common | Flying\nWhen <card_name> enters the battlefield, it explores. (Reveal the top card of your library. Put that card into your hand if it's a land. Otherwise, put a +1/+1 counter on this creature, then put the card back or put it into your graveyard.) | nan |

In [148]:
# Remove all new line characters from the data
card_data = [card.replace('\n', ' ') for card in card_data]

In [149]:
# save the card data to a text file
with open('data/mtg_char/mtg_card_data.txt', 'w') as f:
    f.write(''.join(card_data))

In [150]:
# write out the dataframe to a json file
data.to_json('data/mtg_char/mtg_card_data.json', orient='records', lines=True)

In [151]:
# Create a dataset from the text file
from datasets import load_dataset
dataset = load_dataset('text', data_files='data/mtg_char/mtg_card_data.txt', )


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset text downloaded and prepared to /Users/nickpersing/.cache/huggingface/datasets/text/default-81963d8d2a479985/0.0.0/cb1e9bd71a82ad27976be3b12b407850fe2837d80c22c5e03a28949843a8ace2. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [159]:
# sample the first 10 cards
dataset['train'][:10]


{'text': [' <|endoftext|> Fury Sliver | {5}{R} | Creature — Sliver | uncommon | All Sliver creatures have double strike. | "A rift opened, and our arrows were abruptly stilled. To move was to push the world. But the sliver\'s claw still twitched, red wounds appeared in Thed\'s chest, and ribbons of blood hung in the air." —Adom Capashen, Benalish hero | 3 | 3 <|endoftext|>   <|endoftext|> Kor Outfitter | {W}{W} | Creature — Kor Soldier | common | When <card_name> enters the battlefield, you may attach target Equipment you control to target creature you control. | "We take only what we need to survive. Believe me, you will need this." | 2 | 2 <|endoftext|>   <|endoftext|> Siren Lookout | {2}{U} | Creature — Siren Pirate | common | Flying When <card_name> enters the battlefield, it explores. (Reveal the top card of your library. Put that card into your hand if it\'s a land. Otherwise, put a +1/+1 counter on this creature, then put the card back or put it into your graveyard.) | nan | 1 |

In [106]:
dataset

DatasetDict({
    train: Dataset({
        features: ['text'],
        num_rows: 49367
    })
})

In [107]:
# create a tokenizer

In [153]:
from transformers import GPT2Tokenizer
tokenizer = GPT2Tokenizer.from_pretrained('gpt2', max_length=1024 , pad_to_max_length=True, add_prefix_space=True)
tokenizer.add_special_tokens({'pad_token': '<|pad|>', 'bos_token': '<|startoftext|>', 'eos_token': '<|endoftext|>'})


loading file vocab.json from cache at /Users/nickpersing/.cache/huggingface/hub/models--gpt2/snapshots/e7da7f221d5bf496a48136c0cd264e630fe9fcc8/vocab.json
loading file merges.txt from cache at /Users/nickpersing/.cache/huggingface/hub/models--gpt2/snapshots/e7da7f221d5bf496a48136c0cd264e630fe9fcc8/merges.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at None
loading configuration file config.json from cache at /Users/nickpersing/.cache/huggingface/hub/models--gpt2/snapshots/e7da7f221d5bf496a48136c0cd264e630fe9fcc8/config.json
Model config GPT2Config {
  "_name_or_path": "gpt2",
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "initializer_range": 0.02,
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head":

2

In [154]:
# tokenize the dataset
tokenized_dataset = dataset.map(lambda examples: tokenizer(examples['text'], add_special_tokens=True ), batched=True)



Map:   0%|          | 0/1 [00:00<?, ? examples/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (1955663 > 1024). Running this sequence through the model will result in indexing errors


In [139]:
tokenized_dataset.shape

{'train': (49367, 3)}

In [128]:
# split the dataset into train and validation
tokenized_dataset = tokenized_dataset['train'].train_test_split(test_size=0.2)


In [129]:
# create a model
from transformers import AutoModelForCausalLM
model = AutoModelForCausalLM.from_pretrained('gpt2')


loading configuration file config.json from cache at /Users/nickpersing/.cache/huggingface/hub/models--gpt2/snapshots/e7da7f221d5bf496a48136c0cd264e630fe9fcc8/config.json
Model config GPT2Config {
  "_name_or_path": "gpt2",
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "initializer_range": 0.02,
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 12,
  "n_positions": 1024,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params": {
    "text-generation": {
      "do_sample": true,
      "max_length": 50
    }
  },
  "tran

In [130]:
# train the model
from transformers import Trainer, TrainingArguments
training_args = TrainingArguments(
    output_dir='./results',          # output directory
    num_train_epochs=1,              # total # of training epochs
    per_device_train_batch_size=64,  # batch size per device during training
    per_device_eval_batch_size=64,   # batch size for evaluation
    warmup_steps=500,                # number of warmup steps for learning rate scheduler
    weight_decay=0.01,               # strength of weight decay
    logging_dir='./logs',            # directory for storing logs
    logging_steps=10,
)


PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [131]:
trainer = Trainer(
    model=model,                         # the instantiated 🤗 Transformers model to be trained
    args=training_args,                  # training arguments, defined above
    train_dataset=tokenized_dataset['train'],         # training dataset
    eval_dataset=tokenized_dataset['test'],           # evaluation dataset

)


In [132]:
from transformers.integrations import WandbCallback

# disable the wandb logger
trainer.remove_callback(WandbCallback)

In [144]:
trainer.train()

The following columns in the training set don't have a corresponding argument in `GPT2LMHeadModel.forward` and have been ignored: text. If text are not expected by `GPT2LMHeadModel.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 39493
  Num Epochs = 1
  Instantaneous batch size per device = 64
  Total train batch size (w. parallel, distributed & accumulation) = 64
  Gradient Accumulation steps = 1
  Total optimization steps = 618
  Number of trainable parameters = 124439808


ValueError: expected sequence of length 27 at dim 1 (got 66)

In [147]:
# peek into the tokenized dataset
tokenized_dataset['train'][0]






{'text': ' <|endoftext|> Fury Sliver | {5}{R} | Creature — Sliver | uncommon | All Sliver creatures have double strike. | "A rift opened, and our arrows were abruptly stilled. To move was to push the world. But the sliver\'s claw still twitched, red wounds appeared in Thed\'s chest, and ribbons of blood hung in the air."',
 'input_ids': [220,
  220,
  50256,
  18427,
  3454,
  1428,
  930,
  1391,
  20,
  18477,
  49,
  92,
  930,
  33248,
  851,
  3454,
  1428,
  930,
  19185,
  930,
  1439,
  3454,
  1428,
  8109,
  423,
  4274,
  5587,
  13,
  930,
  366,
  32,
  36788,
  4721,
  11,
  290,
  674,
  20507,
  547,
  25891,
  991,
  276,
  13,
  1675,
  1445,
  373,
  284,
  4574,
  262,
  995,
  13,
  887,
  262,
  1017,
  1428,
  338,
  26573,
  991,
  665,
  10981,
  11,
  2266,
  14129,
  4120,
  287,
  383,
  67,
  338,
  7721,
  11,
  290,
  12183,
  23461,
  286,
  2910,
  9174,
  287,
  262,
  1633,
  526],
 'attention_mask': [1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  